### Data EDA

In [4]:
# Load Required Libraries
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
import os
from IPython.display import HTML
from base64 import b64encode
import cv2

from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


## Train Data Exploration

In [5]:
# View sample video
video_path = '/content/drive/MyDrive/DSAN6600/normanniles1/normanniles1_2025-10-20-07-52-45.mp4'


mp4 = open(video_path,'rb').read()
data_url = "data:video/mp4;base64," + b64encode(mp4).decode()
HTML(f"""
<video width=640 controls>
      <source src="{data_url}" type="video/mp4">
</video>
""")


In [ ]:
# Open train set

train = pd.read_csv('data/train.csv')
train.head()

responseId       view_label  \
0  zYkHaeOdB7XOnvgP3YW5kQs  Norman Niles #1   
1  NYsHaeCRLq-vnvgPjoXZqA0  Norman Niles #1   
2  A40HaYT8KNm7nvgPq8e12AU  Norman Niles #1   
3  EIsHaanDMK-vnvgPjoXZqA0  Norman Niles #1   
4  RYsHafSeMaqpmecP5vCV0AQ  Norman Niles #1   

                                            ID_enter  \
0  time_segment_0_Norman Niles #1_congestion_ente...   
1  time_segment_1_Norman Niles #1_congestion_ente...   
2  time_segment_2_Norman Niles #1_congestion_ente...   
3  time_segment_3_Norman Niles #1_congestion_ente...   
4  time_segment_4_Norman Niles #1_congestion_ente...   

                                             ID_exit  \
0  time_segment_0_Norman Niles #1_congestion_exit...   
1  time_segment_1_Norman Niles #1_congestion_exit...   
2  time_segment_2_Norman Niles #1_congestion_exit...   
3  time_segment_3_Norman Niles #1_congestion_exit...   
4  time_segment_4_Norman Niles #1_congestion_exit...   

                                              videos           video_time  \
0  normanniles1/normanniles1_2025-10-20-06-00-45.mp4  2025-10-20 06:00:45   
1  normanniles1/normanniles1_2025-10-20-06-01-45.mp4  2025-10-20 06:01:45   
2  normanniles1/normanniles1_2025-10-20-06-02-45.mp4  2025-10-20 06:02:45   
3  normanniles1/normanniles1_2025-10-20-06-03-45.mp4  2025-10-20 06:03:45   
4  normanniles1/normanniles1_2025-10-20-06-04-45.mp4  2025-10-20 06:04:45   

   datetimestamp_start    datetimestamp_end        date signaling  \
0  2025-10-20 06:00:45  2025-10-20 06:01:44  2025-10-20      none   
1  2025-10-20 06:01:45  2025-10-20 06:02:44  2025-10-20      none   
2  2025-10-20 06:02:45  2025-10-20 06:03:00  2025-10-20      none   
3  2025-10-20 06:03:45  2025-10-20 06:04:44  2025-10-20      none   
4  2025-10-20 06:04:45  2025-10-20 06:04:59  2025-10-20      none   

  congestion_enter_rating congestion_exit_rating  time_segment_id cycle_phase  
0            free flowing           free flowing                0       train  
1            free flowing           free flowing                1       train  
2            free flowing           free flowing                2       train  
3            free flowing           free flowing                3       train  
4            free flowing           free flowing                4       train

In [ ]:
# View train data properties
train.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 16076 entries, 0 to 16075
Data columns (total 14 columns):
 #   Column                   Non-Null Count  Dtype 
---  ------                   --------------  ----- 
 0   responseId               16076 non-null  object
 1   view_label               16076 non-null  object
 2   ID_enter                 16076 non-null  object
 3   ID_exit                  16076 non-null  object
 4   videos                   16076 non-null  object
 5   video_time               16076 non-null  object
 6   datetimestamp_start      16076 non-null  object
 7   datetimestamp_end        16076 non-null  object
 8   date                     16076 non-null  object
 9   signaling                16076 non-null  object
 10  congestion_enter_rating  16076 non-null  object
 11  congestion_exit_rating   16076 non-null  object
 12  time_segment_id          16076 non-null  int64 
 13  cycle_phase              16076 non-null  object
dtypes: int64(1), object(13)
memory usage: 

In [ ]:
# View unique ID enter and ID exit values
print("Unique ID_Entry values:", train['ID_enter'].nunique())
print("Unique ID_Exit values:", train['ID_exit'].nunique())

Unique ID_Entry values: 16076
Unique ID_Exit values: 16076


In [ ]:
# View the range of train time through the time_segment_id

train['time_segment_id'].describe()

count    16076.000000
mean      2492.425230
std       1445.730463
min          0.000000
25%       1268.000000
50%       2471.000000
75%       3762.000000
max       4986.000000
Name: time_segment_id, dtype: float64

In [ ]:
# Cycle Phase unique values for train
print(train['cycle_phase'].unique())

['train']


## Test Data Exploration

In [ ]:
# Read test set
test = pd.read_csv('data/TestInputSegments.csv')
test.head()

responseId       view_label  \
0   7IkHaYxe2IPY-A_IpprJDA  Norman Niles #1   
1  zIkHaZe0Fr-envgP6uGTmAE  Norman Niles #1   
2  24wHabLnCp__698PweWaiQ4  Norman Niles #1   
3  B4oHaZ3aEuK2nvgPsZGZ4Aw  Norman Niles #1   
4  h4wHaYGCO-aQ2PgPqvKU8As  Norman Niles #1   

                                            ID_enter  \
0  time_segment_112_Norman Niles #1_congestion_en...   
1  time_segment_113_Norman Niles #1_congestion_en...   
2  time_segment_114_Norman Niles #1_congestion_en...   
3  time_segment_115_Norman Niles #1_congestion_en...   
4  time_segment_116_Norman Niles #1_congestion_en...   

                                             ID_exit  \
0  time_segment_112_Norman Niles #1_congestion_ex...   
1  time_segment_113_Norman Niles #1_congestion_ex...   
2  time_segment_114_Norman Niles #1_congestion_ex...   
3  time_segment_115_Norman Niles #1_congestion_ex...   
4  time_segment_116_Norman Niles #1_congestion_ex...   

                                              videos           video_time  \
0  normanniles1/normanniles1_2025-10-20-07-52-45.mp4  2025-10-20 07:52:45   
1  normanniles1/normanniles1_2025-10-20-07-53-45.mp4  2025-10-20 07:53:45   
2  normanniles1/normanniles1_2025-10-20-07-54-45.mp4  2025-10-20 07:54:45   
3  normanniles1/normanniles1_2025-10-20-07-55-45.mp4  2025-10-20 07:55:45   
4  normanniles1/normanniles1_2025-10-20-07-56-45.mp4  2025-10-20 07:56:45   

   datetimestamp_start    datetimestamp_end        date signaling  \
0  2025-10-20 07:52:45  2025-10-20 07:53:44  2025-10-20      none   
1  2025-10-20 07:53:45  2025-10-20 07:54:44  2025-10-20      none   
2  2025-10-20 07:54:45  2025-10-20 07:55:00  2025-10-20      none   
3  2025-10-20 07:55:45  2025-10-20 07:56:44  2025-10-20      none   
4  2025-10-20 07:56:45  2025-10-20 07:57:44  2025-10-20      none   

  congestion_enter_rating congestion_exit_rating  time_segment_id  \
0            free flowing           free flowing              112   
1            free flowing           free flowing              113   
2            free flowing           free flowing              114   
3            free flowing           free flowing              115   
4            free flowing           free flowing              116   

     cycle_phase  
0  test_input_15  
1  test_input_15  
2  test_input_15  
3  test_input_15  
4  test_input_15

In [ ]:
test["congestion_enter_rating"].unique()

array(['free flowing', 'moderate delay', 'heavy delay', 'light delay'],
      dtype=object)

In [ ]:
# View test data properties
test.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 2640 entries, 0 to 2639
Data columns (total 14 columns):
 #   Column                   Non-Null Count  Dtype 
---  ------                   --------------  ----- 
 0   responseId               2640 non-null   object
 1   view_label               2640 non-null   object
 2   ID_enter                 2640 non-null   object
 3   ID_exit                  2640 non-null   object
 4   videos                   2640 non-null   object
 5   video_time               2640 non-null   object
 6   datetimestamp_start      2640 non-null   object
 7   datetimestamp_end        2640 non-null   object
 8   date                     2640 non-null   object
 9   signaling                2640 non-null   object
 10  congestion_enter_rating  2640 non-null   object
 11  congestion_exit_rating   2640 non-null   object
 12  time_segment_id          2640 non-null   int64 
 13  cycle_phase              2640 non-null   object
dtypes: int64(1), object(13)
memory usage: 28

In [ ]:
# View the range of test time through the time_segment_id

test['time_segment_id'].describe()

count    2640.000000
mean     2491.886364
std      1414.431522
min       112.000000
25%      1211.250000
50%      2560.000000
75%      3681.750000
max      4906.000000
Name: time_segment_id, dtype: float64

In [ ]:
# Cycle Phase unique values for test
print(test['cycle_phase'].unique())

Unique values in cycle_phase column:
['test_input_15']

Number of unique cycle_phase values: 1

Value counts for cycle_phase:
cycle_phase
test_input_15    2640
Name: count, dtype: int64


In [ ]:
# View Sample Submission file
sample_submission = pd.read_csv('data/SampleSubmission.csv')
sample_submission.head()

ID        Target  \
0  time_segment_129_Norman Niles #1_congestion_en...  free flowing   
1  time_segment_130_Norman Niles #1_congestion_en...   heavy delay   
2  time_segment_131_Norman Niles #1_congestion_en...  free flowing   
3  time_segment_132_Norman Niles #1_congestion_en...   heavy delay   
4  time_segment_133_Norman Niles #1_congestion_en...  free flowing   

  Target_Accuracy  
0    free flowing  
1     heavy delay  
2    free flowing  
3     heavy delay  
4    free flowing